<h1 align=center><font size = 5>Segmenting and Clustering Neighborhoods in City of Toronto, Canada</font></h1>
<h2 align=center><font size = 5>Applied Data Science Capstone</font></h2>

In [1]:
# importing the necessary libraries
import pandas as pd
import urllib.request
from bs4 import BeautifulSoup
import numpy as np
import requests 
from pandas.io.json import json_normalize
import matplotlib.cm as cm
import matplotlib.colors as colors
from sklearn import preprocessing

### Scrapping Data from Wikipedia

In [2]:
url="https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M"
page=urllib.request.urlopen(url)
soup= BeautifulSoup(page,"lxml")
all_tables=soup.find_all("table")
right_table=soup.find('table', class_='wikitable sortable')

### Transforming the Scrapped Data into a DataFrame

In [3]:
A=[]
B=[]
C=[]
for row in right_table.findAll('tr'):
    cells=row.findAll('td')
    if len(cells)==3:
        A.append(cells[0].find(text=True))
        B.append(cells[1].find(text=True))
        C.append(cells[2].find(text=True))

In [4]:
df=pd.DataFrame(A, columns=['Postal Code'])
df['Borough']=B
df['Neighborhood']=C
df=df[~df.Borough.str.contains("Not assigned")]
df.head()

Postal Code            Borough                                  Neighborhood
2        M3A
        North York
                                    Parkwoods

3        M4A
        North York
                             Victoria Village

4        M5A
  Downtown Toronto
                    Regent Park, Harbourfront

5        M6A
        North York
             Lawrence Manor, Lawrence Heights

6        M7A
  Downtown Toronto
  Queen's Park, Ontario Provincial Government

In [5]:
df['Neighborhood'] = df['Neighborhood'].astype(str)
dr = df.groupby(['Postal Code', 'Borough'])['Neighborhood'].agg( ','.join).reset_index()
dr['Neighborhood']=dr['Neighborhood'].astype(str).map(lambda x: x.rstrip('\n'))
dr['Neighborhood'][dr['Borough']=='Not assigned\n'] = dr['Borough']
dr

Postal Code            Borough  \
0          M1B
       Scarborough
   
1          M1C
       Scarborough
   
2          M1E
       Scarborough
   
3          M1G
       Scarborough
   
4          M1H
       Scarborough
   
5          M1J
       Scarborough
   
6          M1K
       Scarborough
   
7          M1L
       Scarborough
   
8          M1M
       Scarborough
   
9          M1N
       Scarborough
   
10         M1P
       Scarborough
   
11         M1R
       Scarborough
   
12         M1S
       Scarborough
   
13         M1T
       Scarborough
   
14         M1V
       Scarborough
   
15         M1W
       Scarborough
   
16         M1X
       Scarborough
   
17         M2H
        North York
   
18         M2J
        North York
   
19         M2K
        North York
   
20         M2L
        North York
   
21         M2M
        North York
   
22         M2N
        North York
   
23         M2P
        North York
   
24         M2R
        North York
   
25         M3A
        North York
   
26         M3B
        North York
   
27         M3C
        North York
   
28         M3H
        North York
   
29         M3J
        North York
   
..          ...                ...   
73         M6C
              York
   
74         M6E
              York
   
75         M6G
  Downtown Toronto
   
76         M6H
      West Toronto
   
77         M6J
      West Toronto
   
78         M6K
      West Toronto
   
79         M6L
        North York
   
80         M6M
              York
   
81         M6N
              York
   
82         M6P
      West Toronto
   
83         M6R
      West Toronto
   
84         M6S
      West Toronto
   
85         M7A
  Downtown Toronto
   
86         M7R
       Mississauga
   
87         M7Y
      East Toronto
   
88         M8V
         Etobicoke
   
89         M8W
         Etobicoke
   
90         M8X
         Etobicoke
   
91         M8Y
         Etobicoke
   
92         M8Z
         Etobicoke
   
93         M9A
         Etobicoke
   
94         M9B
         Etobicoke
   
95         M9C
         Etobicoke
   
96         M9L
        North York
   
97         M9M
        North York
   
98         M9N
              York
   
99         M9P
         Etobicoke
   
100        M9R
         Etobicoke
   
101        M9V
         Etobicoke
   
102        M9W
         Etobicoke
   

                                          Neighborhood  
0                                       Malvern, Rouge  
1               Rouge Hill, Port Union, Highland Creek  
2                    Guildwood, Morningside, West Hill  
3                                               Woburn  
4                                            Cedarbrae  
5                                  Scarborough Village  
6          Kennedy Park, Ionview, East Birchmount Park  
7                      Golden Mile, Clairlea, Oakridge  
8      Cliffside, Cliffcrest, Scarborough Village West  
9                          Birch Cliff, Cliffside West  
10   Dorset Park, Wexford Heights, Scarborough Town...  
11                                   Wexford, Maryvale  
12                                           Agincourt  
13             Clarks Corners, Tam O'Shanter, Sullivan  
14   Milliken, Agincourt North, Steeles East, L'Amo...  
15                       Steeles West, L'Amoreaux West  
16                                         Upper Rouge  
17                                   Hillcrest Village  
18                        Fairview, Henry Farm, Oriole  
19                                     Bayview Village  
20                            York Mills, Silver Hills  
21                             Willowdale, Newtonbrook  
22                         Willowdale, Willowdale East  
23                                     York Mills West  
24                         Willowdale, Willowdale West  
25                                           Parkwoods  
26                                           Don Mills  
27                                           Don Mi

In [6]:
dr.shape

(103, 3)

In [7]:
dr['Postal Code']= dr['Postal Code'].astype(str).map(lambda x: x.rstrip('\n'))

In [8]:
!wget -O Geospatial_data.csv http://cocl.us/Geospatial_data
dx=pd.read_csv("Geospatial_data.csv")
dx.head()

--2020-06-27 10:01:21--  http://cocl.us/Geospatial_data
Resolving cocl.us (cocl.us)... 158.85.108.83, 158.85.108.86, 169.48.113.194
Connecting to cocl.us (cocl.us)|158.85.108.83|:80... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: https://cocl.us/Geospatial_data [following]
--2020-06-27 10:01:21--  https://cocl.us/Geospatial_data
Connecting to cocl.us (cocl.us)|158.85.108.83|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: https://ibm.box.com/shared/static/9afzr83pps4pwf2smjjcf1y5mvgb18rr.csv [following]
--2020-06-27 10:01:23--  https://ibm.box.com/shared/static/9afzr83pps4pwf2smjjcf1y5mvgb18rr.csv
Resolving ibm.box.com (ibm.box.com)... 185.235.236.197
Connecting to ibm.box.com (ibm.box.com)|185.235.236.197|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: /public/static/9afzr83pps4pwf2smjjcf1y5mvgb18rr.csv [following]
--2020-06-27 10:01:24--  https://ibm.box.com/publ

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [9]:
result = pd.merge(dr,dx, how='left', on=['Postal Code', 'Postal Code'])
result.head()

Postal Code       Borough                            Neighborhood  \
0         M1B  Scarborough
                          Malvern, Rouge   
1         M1C  Scarborough
  Rouge Hill, Port Union, Highland Creek   
2         M1E  Scarborough
       Guildwood, Morningside, West Hill   
3         M1G  Scarborough
                                  Woburn   
4         M1H  Scarborough
                               Cedarbrae   

    Latitude  Longitude  
0  43.806686 -79.194353  
1  43.784535 -79.160497  
2  43.763573 -79.188711  
3  43.770992 -79.216917  
4  43.773136 -79.239476

### Defining Foursquare Credentials and Version
Looking for restaurants in 2 kilometer radius of each pincode location.

In [10]:
# The code was removed by Watson Studio for sharing.

restaurant......ok


In [11]:
# The code was removed by Watson Studio for sharing.

In [13]:
extract= requests.get(url).json()
# assign relevant part of JSON to venues
venues = extract['response']['venues']

# tranform venues into a dataframe
df1_test = json_normalize(venues)
dataframe=pd.DataFrame(columns=df1_test.columns)
df1={}
for i in range(len(result)):
    url = 'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'.format(CLIENT_ID, CLIENT_SECRET,result['Latitude'][i],result['Longitude'][i], VERSION, search_query, radius, LIMIT)
    extract= requests.get(url).json()
    venues = extract['response']['venues']
    df1[i] = json_normalize(venues)
    dataframe.append(df1[i])

In [14]:
compiled_dataframe=pd.DataFrame(columns=df1_test.columns)
for i in range(len(result)):
    compiled_dataframe=pd.concat([compiled_dataframe,df1[i]],axis=0)
    
compiled_dataframe=compiled_dataframe.reset_index(drop=True)
compiled_dataframe.head()

/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:3: FutureWarning: Sorting because non-concatenation axis is not aligned. A future version
of pandas will change to not sort by default.

To accept the future behavior, pass 'sort=False'.

To retain the current behavior and silence the warning, pass 'sort=True'.

  app.launch_new_instance()


categories hasPerk  \
0  [{'id': '4bf58dd8d48988d143941735', 'name': 'B...   False   
1  [{'id': '4bf58dd8d48988d1f9941735', 'name': 'F...   False   
2  [{'id': '4bf58dd8d48988d1c4941735', 'name': 'R...   False   
3  [{'id': '4bf58dd8d48988d16c941735', 'name': 'B...   False   
4  [{'id': '4bf58dd8d48988d144941735', 'name': 'C...   False   

                         id      location.address location.cc  \
0  4be6c179d4f7c9b665042720  404 Old Kingston Rd.          CA   
1  4c97a82382b56dcbf7afebaa                   NaN          CA   
2  51f2c1f8498edf6fd71b8e18                   NaN          CA   
3  4b96cbe6f964a5202ae534e3      1265 Military Tr          CA   
4  5144fe0fe4b0634be203f271   5780 Sheppard Ave E          CA   

      location.city location.country location.crossStreet location.distance  \
0       Scarborough           Canada                  NaN              3194   
1  Toronto Division           Canada                  NaN              1636   
2               NaN           Canada                  NaN              3042   
3           Toronto           Canada                  NaN              2485   
4           Toronto           Canada           Markham Rd              3276   

                           location.formattedAddress  \
0     [404 Old Kingston Rd., Scarborough ON, Canada]   
1                      [Toronto Division ON, Canada]   
2                                           [Canada]   
3             [1265 Military Tr, Toronto ON, Canada]   
4  [5780 Sheppard Ave E (Markham Rd), Toronto ON,...   

                             location.labeledLatLngs  location.lat  \
0  [{'label': 'display', 'lat': 43.78446796744621...     43.784468   
1  [{'label': 'display', 'lat': 43.81958724358436...     43.819587   
2  [{'label': 'display', 'lat': 43.78047180175781...     43.780472   
3  [{'label': 'display', 'lat': 43.78500731279124...     43.785007   
4  [{'label': 'display', 'lat': 43.79554878818409...     43.795549   

   location.lng location.neighborhood location.postalCode location.state  \
0    -79.169200                   NaN                 NaN             ON   
1    -79.184574                   NaN                 NaN             ON   
2    -79.205078           Morningside                 NaN            NaN   
3    -79.186964                   NaN                 NaN             ON   
4    -79.232105                   NaN                 NaN             ON   

                   name    referralId venuePage.id  
0      Ted's Restaurant  v-1593252161          NaN  
1     Africa Restaurant  v-1593252161          NaN  
2  Grapevine Restaurant  v-1593252161          NaN  
3  Rex's Den Restaurant  v-1593252161          NaN  
4    Sabby's Restaurant  v-1593252161          NaN

In [15]:
# keep only columns that include venue name, and anything that is associated with location
filtered_columns = ['name', 'categories'] + [col for col in compiled_dataframe.columns if col.startswith('location.')] + ['id']
dataframe_filtered = compiled_dataframe.loc[:, filtered_columns]

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

# filter the category for each row
dataframe_filtered['categories'] = dataframe_filtered.apply(get_category_type, axis=1)

# clean column names by keeping only last term
dataframe_filtered.columns = [column.split('.')[-1] for column in dataframe_filtered.columns]

dataframe_filtered.head()

name            categories               address  cc  \
0      Ted's Restaurant        Breakfast Spot  404 Old Kingston Rd.  CA   
1     Africa Restaurant     Food & Drink Shop                   NaN  CA   
2  Grapevine Restaurant            Restaurant                   NaN  CA   
3  Rex's Den Restaurant          Burger Joint      1265 Military Tr  CA   
4    Sabby's Restaurant  Caribbean Restaurant   5780 Sheppard Ave E  CA   

               city country crossStreet distance  \
0       Scarborough  Canada         NaN     3194   
1  Toronto Division  Canada         NaN     1636   
2               NaN  Canada         NaN     3042   
3           Toronto  Canada         NaN     2485   
4           Toronto  Canada  Markham Rd     3276   

                                    formattedAddress  \
0     [404 Old Kingston Rd., Scarborough ON, Canada]   
1                      [Toronto Division ON, Canada]   
2                                           [Canada]   
3             [1265 Military Tr, Toronto ON, Canada]   
4  [5780 Sheppard Ave E (Markham Rd), Toronto ON,...   

                                      labeledLatLngs        lat        lng  \
0  [{'label': 'display', 'lat': 43.78446796744621...  43.784468 -79.169200   
1  [{'label': 'display', 'lat': 43.81958724358436...  43.819587 -79.184574   
2  [{'label': 'display', 'lat': 43.78047180175781...  43.780472 -79.205078   
3  [{'label': 'display', 'lat': 43.78500731279124...  43.785007 -79.186964   
4  [{'label': 'display', 'lat': 43.79554878818409...  43.795549 -79.232105   

  neighborhood postalCode state                        id  
0          NaN        NaN    ON  4be6c179d4f7c9b665042720  
1          NaN        NaN    ON  4c97a82382b56dcbf7afebaa  
2  Morningside        NaN   NaN  51f2c1f8498edf6fd71b8e18  
3          NaN        NaN    ON  4b96cbe6f964a5202ae534e3  
4          NaN        NaN    ON  5144fe0fe4b0634be203f271

In [16]:
!conda install -c conda-forge folium=0.5.0 --yes
import folium # plotting library

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - folium=0.5.0


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    openssl-1.1.1g             |       h516909a_0         2.1 MB  conda-forge
    ca-certificates-2020.6.20  |       hecda079_0         145 KB  conda-forge
    folium-0.5.0               |             py_0          45 KB  conda-forge
    vincent-0.4.4              |             py_1          28 KB  conda-forge
    altair-4.1.0               |             py_1         614 KB  conda-forge
    branca-0.4.1               |             py_0          26 KB  conda-forge
    python_abi-3.6             |          1_cp36m           4 KB  conda-forge
    certifi-2020.6.20          |   py36h9f0ad1d_0         151 KB  conda-forge
    ------------------------------------------------------------
                       

In [17]:
dataframe_filtered=dataframe_filtered[~dataframe_filtered['id'].apply(pd.Series).duplicated()]
dataframe_filtered = dataframe_filtered.reset_index()
dataframe_filtered.head()

index                  name            categories               address  \
0      0      Ted's Restaurant        Breakfast Spot  404 Old Kingston Rd.   
1      1     Africa Restaurant     Food & Drink Shop                   NaN   
2      2  Grapevine Restaurant            Restaurant                   NaN   
3      3  Rex's Den Restaurant          Burger Joint      1265 Military Tr   
4      4    Sabby's Restaurant  Caribbean Restaurant   5780 Sheppard Ave E   

   cc              city country crossStreet distance  \
0  CA       Scarborough  Canada         NaN     3194   
1  CA  Toronto Division  Canada         NaN     1636   
2  CA               NaN  Canada         NaN     3042   
3  CA           Toronto  Canada         NaN     2485   
4  CA           Toronto  Canada  Markham Rd     3276   

                                    formattedAddress  \
0     [404 Old Kingston Rd., Scarborough ON, Canada]   
1                      [Toronto Division ON, Canada]   
2                                           [Canada]   
3             [1265 Military Tr, Toronto ON, Canada]   
4  [5780 Sheppard Ave E (Markham Rd), Toronto ON,...   

                                      labeledLatLngs        lat        lng  \
0  [{'label': 'display', 'lat': 43.78446796744621...  43.784468 -79.169200   
1  [{'label': 'display', 'lat': 43.81958724358436...  43.819587 -79.184574   
2  [{'label': 'display', 'lat': 43.78047180175781...  43.780472 -79.205078   
3  [{'label': 'display', 'lat': 43.78500731279124...  43.785007 -79.186964   
4  [{'label': 'display', 'lat': 43.79554878818409...  43.795549 -79.232105   

  neighborhood postalCode state                        id  
0          NaN        NaN    ON  4be6c179d4f7c9b665042720  
1          NaN        NaN    ON  4c97a82382b56dcbf7afebaa  
2  Morningside        NaN   NaN  51f2c1f8498edf6fd71b8e18  
3          NaN        NaN    ON  4b96cbe6f964a5202ae534e3  
4          NaN        NaN    ON  5144fe0fe4b0634be203f271

### Plotting the Location of Restaurants

In [18]:
venues_map = folium.Map(location=[43.742778, -79.465556], zoom_start=12) # generate map centred around the Conrad Hotel


# add the Italian restaurants as blue circle markers
for lat, lng, label in zip(dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.categories):
    folium.features.CircleMarker(
        [lat, lng],
        radius=5,
        color='blue',
        popup=label,
        fill = True,
        fill_color='blue',
        fill_opacity=0.6
    ).add_to(venues_map)

# display map
venues_map

In [19]:
! pip freeze   # optional: this is to check current installed package
! pip install plotly --upgrade   # this to update plotly to latest version, at the time of this post: 4.5.4
! pip install plotly   # might be unnecessary, but I did this
import plotly.express as px   # now it works

absl-py==0.7.0
alabaster==0.7.12
altair==4.1.0
anaconda-client==1.7.2
anaconda-project==0.8.2
arcgis==1.6.0
asn1crypto==0.24.0
astor==0.7.1
astroid==2.1.0
astropy==3.1.1
astunparse==1.6.2
atomicwrites==1.3.0
attrs==18.2.0
autoai-libs==1.10.5
Babel==2.6.0
backcall==0.1.0
backports.os==0.1.1
backports.shutil-get-terminal-size==1.0.0
beautifulsoup4==4.7.1
biopython==1.72
bitarray==0.8.3
bkcharts==0.2
blaze==0.11.3
bleach==3.1.0
bokeh==1.0.4
boto==2.49.0
boto3==1.9.82
botocore==1.12.82
Bottleneck==1.2.1
branca==0.4.1
brunel==2.3
ca-data-connector==11.1.7
category-encoders==2.0.0
certifi==2020.6.20
cffi==1.11.5
chardet==3.0.4
Click==7.0
cloudpickle==0.7.0
clyent==1.2.2
colorama==0.4.1
colour==0.1.5
contextlib2==0.5.5
cplex==12.10.0.1
cryptography==2.5
cx-Oracle==7.0.0
cycler==0.10.0
Cython==0.29.5
cytoolz==0.9.0.1
dask==1.1.1
datashape==0.5.4
decorator==4.3.2
defusedxml==0.5.0
dill==0.2.8.2
distributed==1.25.3
docloud==1.0.375
docplex==2.14.186
docutils==0.14
entrypoints==0.3
et-xmlfile==1.

### Count of Different Types of Restaurants

In [20]:
restaurant_counter=dataframe_filtered['categories'].value_counts()
restaurant_counter=restaurant_counter.reset_index()
restaurant_counter=restaurant_counter.rename(columns={"index": "categories", "categories": "count"})
restaurant_counter

categories  count
0                          Chinese Restaurant    141
1                                  Restaurant    110
2                        Caribbean Restaurant     46
3                           Korean Restaurant     40
4                           Indian Restaurant     37
5                            Asian Restaurant     36
6                   Middle Eastern Restaurant     34
7                         Japanese Restaurant     29
8                                       Diner     27
9                          Italian Restaurant     24
10                        American Restaurant     23
11                      Vietnamese Restaurant     22
12                             Breakfast Spot     22
13                                        Bar     20
14                         African Restaurant     15
15                             Sandwich Place     14
16                            Thai Restaurant     13
17                       Ethiopian Restaurant     12
18                           Sushi Restaurant     12
19                           Greek Restaurant     11
20                Eastern European Restaurant     11
21                  Latin American Restaurant     10
22                        Filipino Restaurant      9
23                         Turkish Restaurant      7
24                    New American Restaurant      7
25                          French Restaurant      6
26                   Mediterranean Restaurant      6
27                       Cantonese Restaurant      6
28                      Portuguese Restaurant      6
29                               Burger Joint      5
..                                        ...    ...
80                                Wings Joint      1
81                         Persian Restaurant      1
82                    Scandinavian Restaurant      1
83                        Moroccan Restaurant      1
84                           Hunan Restaurant      1
85                         English Restaurant      1
86                                   Dive Bar      1
87                         Mac & Cheese Joint      1
88                        Peruvian Restaurant      1
89                                 Bagel Shop      1
90                                Other Event      1
91                  South American Restaurant      1
92                     Argentinian Restaurant      1
93                           Czech Restaurant      1
94                           Theme Restaurant      1
95            Southern / Soul Food Restaurant      1
96                            Coworking Space      1
97                                Music Venue      1
98                             Hardware Store      1
99                                   Vineyard      1
100                                    Bakery      1
101                   South Indian Restaurant      1
102           Molecular Gastronomy Restaurant      1
103                            Nightlife Spot      1
104  Residential Building (Apartment / Condo)      1
105                             Grocery Store      1
106                       Dumpling Restaurant      1
107                         Polish Restaurant      1
108                                Hookah Bar      1
109                                 Juice Bar      1

[110 rows x 2 columns]

In [21]:
fig1 = px.bar(x=restaurant_counter["categories"], y=restaurant_counter["count"])
fig1.update_layout(
    xaxis_title="Categories",
    yaxis_title="Count",xaxis_type='category',
    title_text='Distribution of different types of restaurants')
fig1.show()

### Count of the Number of Restaurants in Each City

In [22]:
city_counter=dataframe_filtered['city'].value_counts()
city_counter=city_counter.reset_index()
city_counter=city_counter.dropna()
city_counter=city_counter.rename(columns={"index": "City", "city": "count"})
city_counter

City  count
0               Toronto    588
1           Scarborough     71
2           Mississauga     36
3             Etobicoke     33
4            North York     33
5               Markham     15
6               Vaughan     14
7             Thornhill      8
8            Woodbridge      8
9      Toronto Division      6
10            East York      5
11              Concord      4
12                 York      3
13              Rexdale      2
14  Black Creek village      1
15               Vaughn      1
16          Port Credit      1
17               Torono      1
18        Richmond Hill      1
19              Niagara      1
20             Edmonton      1
21              Oakvill      1
22               Dundas      1
23           Willowdale      1
24              toronto      1
25               Bolton      1
26           Grand Case      1
27              Vahalla      1
28            Cambridge      1
29          Scarboroigh      1
30       Weston Village      1

In [23]:
fig2 = px.bar(x=city_counter["City"], y=city_counter["count"])
fig2.update_layout(
    xaxis_title="City",
    yaxis_title="Number of restaurants",xaxis_type='category',
    title_text='Distribution of restaurants in different cities')
fig2.show()

In [24]:
group_data=dataframe_filtered.groupby(['categories','city']).count().reset_index()
group_data=group_data[['categories','city','name']]
group_data=group_data.rename(columns={'name':'count'})
group_data

categories              city  count
0                  Afghan Restaurant        North York      1
1                  Afghan Restaurant           Toronto      1
2                 African Restaurant         Etobicoke      2
3                 African Restaurant           Toronto      8
4                 African Restaurant    Weston Village      1
5                American Restaurant         Etobicoke      1
6                American Restaurant       Mississauga      3
7                American Restaurant       Scarborough      1
8                American Restaurant           Toronto     13
9             Argentinian Restaurant           Toronto      1
10                  Asian Restaurant         Etobicoke      1
11                  Asian Restaurant           Markham      1
12                  Asian Restaurant       Mississauga      1
13                  Asian Restaurant       Scarborough      4
14                  Asian Restaurant           Toronto     22
15                         BBQ Joint           Toronto      2
16                        Bagel Shop        North York      1
17                            Bakery           Toronto      1
18                               Bar       Mississauga      1
19                               Bar        North York      2
20                               Bar       Scarborough      1
21                               Bar           Toronto     12
22                            Bistro           Toronto      3
23              Brazilian Restaurant           Toronto      1
24                    Breakfast Spot         Etobicoke      2
25                    Breakfast Spot       Mississauga      1
26                    Breakfast Spot       Scarborough      1
27                    Breakfast Spot           Toronto     14
28                    Breakfast Spot           Vaughan      1
29                          Building           Toronto      1
..                               ...               ...    ...
200        South American Restaurant       Mississauga      1
201          South Indian Restaurant  Toronto Division      1
202  Southern / Soul Food Restaurant           Toronto      1
203               Spanish Restaurant           Toronto      3
204                       Steakhouse       Mississauga      2
205                       Steakhouse         Thornhill      1
206                       Steakhouse           Toronto      2
207                 Sushi Restaurant         Etobicoke      2
208                 Sushi Restaurant           Toronto     10
209              Szechuan Restaurant        North York      1
210              Szechuan Restaurant           Toronto      1
211                  Thai Restaurant           Concord      1
212                  Thai Restaurant         Etobicoke      1
213                  Thai Restaurant           Toronto      9
214                  Thai Restaurant  Toronto Division      1
215                 Theme Restaurant           Toronto      1
216               Tibetan Restaurant           Toronto      1
217               Turkish Restaurant       Mississauga      1
218               Turkish Restaurant           Toronto      6
219    Vegetarian / Vegan Restaurant       Scarborough      1
220    Vegetarian / Vegan Restaurant           Toronto      3
221            Vietnamese Restaurant       Mississauga      2
222            Vietnamese Restaurant       Scarborough      2
223            Vietnamese Restaurant           Toronto     14
224                         Vineyard           Toronto      1
225                  Warehouse Store           Toronto      1
226                         Wine Bar           Toronto      1
227                      Wings Joint        North York      1
228              Xinjiang Restaurant           Markham      1
229              Xinjiang Restaurant       Mississauga      1

[230 rows x 3 columns]

In [25]:
fig3 = px.bar(group_data, x="city", y="count", color="categories",barmode="group")
fig3.update_layout(title="Distribution of Different types of Restaurants in Different Cities",
    xaxis_title="Categories",
    yaxis_title="Number of Restaurants",xaxis_type='category',
    width=10000,
    height=800)
fig3.show()

In [26]:
d = dict([(y,x+1) for x,y in enumerate(sorted(set(dataframe_filtered['categories'].astype(str))))])

In [27]:
connect=pd.DataFrame.from_dict(d, orient='index').reset_index().rename(columns={"index":"categories",0:"num"})
dataframe_filtered = pd.merge(dataframe_filtered,connect, how='left', on=['categories', 'categories'])
dataframe_filtered['num']=dataframe_filtered['num'].fillna(77)
dataframe_filtered

index                                             name  \
0        0                                 Ted's Restaurant   
1        1                                Africa Restaurant   
2        2                             Grapevine Restaurant   
3        3                             Rex's Den Restaurant   
4        4                               Sabby's Restaurant   
5        5                                          Wendy’s   
6        8                         Peking Garden Restaurant   
7        9                                 Mahar Restaurant   
8       10                 Wonder Season Chinese Restaurant   
9       11                                       McDonald's   
10      15                        Little Bavaria Restaurant   
11      16                               Tai Chi Restaurant   
12      19                       Sunny's Bar and Restaurant   
13      21                                Prague Restaurant   
14      23                 Spice It Up Caribbean Restaurant   
15      24           Ali Baba's Restaurant @ Cedarbrae Mall   
16      25                         Sa-Fire Restaurant & Bar   
17      26                                 Max's Restaurant   
18      27                         Woburn Garden Restaurant   
19      28                                           Subway   
20      29                                      Lucky Hakka   
21      30                                           Subway   
22      33                        Sammy's Family Restaurant   
23      39                       Markham Station Restaurant   
24      41                         Terry's Restaurant & Bar   
25      42                               terry's restaurant   
26      46                                       McDonald's   
27      47                               Terry's Restaurant   
28      49                              Federick Restaurant   
29      50                        The Local Cafe Restaurant   
..     ...                                              ...   
930   3647                            Quatrefoil Restaurant   
931   3651                                            Ginko   
932   3652                             Tucker's Marketplace   
933   3653                            Shanghai's restaurant   
934   3654                        Dallas Restaurant And Bar   
935   3655                                Honest Restaurant   
936   3657                      24Seven Lounge & Restaurant   
937   3658                     24 Seven Lounge & Restaurant   
938   3667                             Favorites Restaurant   
939   3669                     Sunrise Caribbean Restaurant   
940   3671                                 Bilal Restaurant   
941   3672                                 Bilal Restaurant   
942   3673                   Spotlight caribbean restaurant   
943   3677                                  Mandarin Buffet   
944   3679              Caribbean Oasis Lounge & Restaurant   
945   3685                           Bliss Restaurant & Bar   
946   3688     Fairfield Inn & Suites restaurant and lounge   
947   3692                      The Metropolitan Restaurant   
948   3693  Bliss Restaurant & Bar - Hilton Airport Toronto   
949   3694                                 Zet's Restaurant   
950   3699                                     Meteor Diner   
951   3700                               Fifty's restaurant   
952   3701    Fuzion Restaurant (Grill-Steakhouse-Tandoori)   
953   3702                              PizzaWay Restaurant   
954   3703                    Falls Manor Family Restaurant   
955   3705                               Simma's Restaurant   
956   3706        Sky's The Limit - Lolo's Bar & Restaurant   
957   3707                The Local Restaurant And Wine Bar   
958   3710                                            Corso   
959   3711             Topiary's Steak & Seafood Restaurant   

                    categories                             address  cc  \
0               Breakfas

### Location Plot of Restaurant Types

In [28]:
venues_map1 = folium.Map(location=[43.742778, -79.465556], zoom_start=12) 
d_len=len(d)
x = np.arange(d_len)
ys = [i + x + (i*x)**2 for i in range(d_len)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]
markers_colors=[]
for name,categories,lat, lng, numt in zip(dataframe_filtered.name,dataframe_filtered.categories,dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.num.astype(int)):
    label = folium.Popup( str(name) + ' |  Category :' + str(categories), parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color=rainbow[numt-1],
        fill = True,
        fill_color=rainbow[numt-1],
        fill_opacity=0.6
    ).add_to(venues_map1)

# display map
venues_map1

In [29]:
from sklearn.cluster import KMeans
# import warnings filter
import warnings
from warnings import simplefilter
# ignore all future warnings
simplefilter(action='ignore', category=FutureWarning)

In [30]:
points=[[0]*2]*len(dataframe_filtered) 
for i in range(len(dataframe_filtered)):
    points[i][0]=float(dataframe_filtered['lat'][i])
    points[i][1]=float(dataframe_filtered['lng'][i])

In [31]:
X=dataframe_filtered[['lat','lng']]
X = preprocessing.StandardScaler().fit(X).transform(X.astype(float))

In [32]:
kclusters = 20
restaurant_clustering1 =dataframe_filtered[['lat','lng']]
kmeans5 = KMeans(n_clusters=kclusters, random_state=0).fit(X)
kmeans5.labels_[0:10]

array([13,  2, 13, 13,  2, 13, 13, 13, 13, 13], dtype=int32)

In [33]:
dataframe_filtered.insert(0, 'ClusterLabels', kmeans5.labels_)
dataframe_filtered.head()

ClusterLabels  index                  name            categories  \
0             13      0      Ted's Restaurant        Breakfast Spot   
1              2      1     Africa Restaurant     Food & Drink Shop   
2             13      2  Grapevine Restaurant            Restaurant   
3             13      3  Rex's Den Restaurant          Burger Joint   
4              2      4    Sabby's Restaurant  Caribbean Restaurant   

                address  cc              city country crossStreet distance  \
0  404 Old Kingston Rd.  CA       Scarborough  Canada         NaN     3194   
1                   NaN  CA  Toronto Division  Canada         NaN     1636   
2                   NaN  CA               NaN  Canada         NaN     3042   
3      1265 Military Tr  CA           Toronto  Canada         NaN     2485   
4   5780 Sheppard Ave E  CA           Toronto  Canada  Markham Rd     3276   

                                    formattedAddress  \
0     [404 Old Kingston Rd., Scarborough ON, Canada]   
1                      [Toronto Division ON, Canada]   
2                                           [Canada]   
3             [1265 Military Tr, Toronto ON, Canada]   
4  [5780 Sheppard Ave E (Markham Rd), Toronto ON,...   

                                      labeledLatLngs        lat        lng  \
0  [{'label': 'display', 'lat': 43.78446796744621...  43.784468 -79.169200   
1  [{'label': 'display', 'lat': 43.81958724358436...  43.819587 -79.184574   
2  [{'label': 'display', 'lat': 43.78047180175781...  43.780472 -79.205078   
3  [{'label': 'display', 'lat': 43.78500731279124...  43.785007 -79.186964   
4  [{'label': 'display', 'lat': 43.79554878818409...  43.795549 -79.232105   

  neighborhood postalCode state                        id   num  
0          NaN        NaN    ON  4be6c179d4f7c9b665042720  12.0  
1          NaN        NaN    ON  4c97a82382b56dcbf7afebaa  35.0  
2  Morningside        NaN   NaN  51f2c1f8498edf6fd71b8e18  90.0  
3          NaN        NaN    ON  4b96cbe6f964a5202ae534e3  14.0  
4          NaN        NaN    ON  5144fe0fe4b0634be203f271  17.0

### Clustering Restaurants in the Neighborhood based on Proximity

In [34]:
venues_map2 = folium.Map(location=[43.742778, -79.465556], zoom_start=12) 

x1 = np.arange(kclusters)
ys1 = [i + x1 + (i*x1)**2 for i in range(kclusters)]
colors_array1 = cm.rainbow(np.linspace(0, 1, len(ys1)))
rainbow1 = [colors.rgb2hex(i) for i in colors_array1]
markers_colors=[]
for name,cluster,categories,lat, lng, numt in zip(dataframe_filtered.name,dataframe_filtered.ClusterLabels,dataframe_filtered.categories,dataframe_filtered.lat, dataframe_filtered.lng, dataframe_filtered.num.astype(int)):
    label = folium.Popup( str(name) + ' |  Category :' + str(categories) + ' | Cluster :'+ str(cluster), parse_html=True)
    
    folium.CircleMarker(
        [lat, lng],
        radius=2,
        popup=label,
        color=rainbow1[cluster-1],
        fill=True,
        fill_color=rainbow1[cluster-1],
        fill_opacity=0.7).add_to(venues_map2)

# display map
venues_map2
